In [8]:
import pandas as pd
import xlrd
import numpy as np
import json
import geonamescache
from geopy.geocoders import Nominatim

In [2]:
not_states = ["MP", "PR", "AS", "UM", "VI", "GU"]
with open("tools/state_codes.json", 'r') as f:
    state_codes = json.load(f)
    states_list = [key for key in state_codes if key not in not_states and state_codes[key] not in not_states]

In [93]:
gl = Nominatim(user_agent="hacklytics23")
gc = geonamescache.GeonamesCache()

In [4]:
pd.set_option('display.max_rows', None)
pd.options.mode.chained_assignment = None

In [161]:
cache = {}

In [338]:
exceptions = {
    ('Florence', 'AL'): 'Lauderdale',
    ('Batesville', 'AR'): 'Independence',
    ('Auburn', 'CA'): 'Placer', 
    ('Willows', 'CA'): 'Glenn',
    ('Yuba City', 'CA'): 'Sutter',
    ('Placerville', 'CA'): 'El Dorado',
    ('Jackson', 'CA'): 'Amador',
    ('Red Bluff', 'CA'): 'Tehama',
    ('Lucerne', 'CA'): 'Lake',
    ('Bishop', 'CA'): 'Inyo',
    ('Ft Walton Beach', 'FL'): 'Okaloosa',
    ('Vero Beach', 'FL'): 'Indian River',
    ('St. Augustine', 'FL'): 'St. Johns',
    ('Avon Park', 'FL'): 'Highlands',
    ('Lake City', 'FL'): 'Columbia',
    ('New Port Richey', 'FL'): 'Pasco',
    ('Inverness', 'FL'): 'Citrus',
    ('Naples', 'FL'): 'Collier',
    ('Decatur', 'GA'): 'DeKalb',
    ('Pearl City', 'HI'): 'Honolulu',
    ('Sioux City', 'IA'): 'Woodbury',
    ('Cedar Rapids', 'IA'): 'Linn',
    ('McHenry', 'IL'): 'McHenry',
    ('Des Moines', 'IL'): 'Polk',
    ('Edwardsville', 'IL'): 'Madison',
    ('Hillside', 'IL'): 'Cook',
    ('Wheaton', 'IL'): 'DuPage',
    ('Greenup', 'IL'): 'Cumberland',
	('Geneva', 'IL'): 'Kane',
	('Olney', 'IL'): 'Richland',
	('Mandeville', 'LA'): 'St. Tammany',
	('Alexandria', 'LA'): 'Rapides',
	('Greenfield', 'MA'): 'Franklin',
	('Lexington Park', 'MD'): 'St. Mary\'s',
	('Oakland', 'MD'): 'Garrett',
	('Westover', 'MD'): 'Somerset',
	('Lanham', 'MD'): 'Prince George\'s',
	('Wyandotte', 'MI'): 'Wayne',
	('Mount Clemens', 'MI'): 'Macomb',
	('Traverse City', 'MI'): 'Grand Traverse',
	('Battle Creek', 'MI'): 'Calhoun',
	('Battle Creek', 'MI'): 'Calhoun',
	('Muskegon', 'MI'): 'Muskegon',
	('Howell', 'MI'): 'Livingston',
	('Charlotte', 'MI'): 'Eaton',
	('Des Moines', 'MN'): 'Jackson',
	('Zumbrota', 'MN'): 'Goodhue',
	('St. Augusta', 'MN'): 'Stearns',
	('Bemidji', 'MN'): 'Beltrami',
	('Dilworth', 'MN'): 'Clay',
	('Slayton', 'MN'): 'Murray',
	('Cottleville', 'MO'): 'St. Charles',
	('St. Peters', 'MO'): 'St. Charles',
	('Sidney', 'MT'): 'Richland',
	('Lansing', 'NC'): 'Ashe',
	('High Point', 'NC'): 'Guilford',
	('Gastonia', 'NC'): 'Gaston',
	('Hillsborough', 'NC'): 'Orange',
	('Mount Holly', 'NJ'): 'Burlington',
	('Freehold', 'NJ'): 'Monmouth',
	('Cranford', 'NJ'): 'Union',
	('Salem', 'NJ'): 'Salem',
	('Somerville', 'NJ'): 'Somerset',
	('Newton', 'NJ'): 'Sussex',
	('Gowanda', 'NY'): '',
	('Clifton Springs', 'NY'): 'Ontario',
	('Dunkirk', 'NY'): 'Chautauqua',
	('Amityville', 'NY'): 'Suffolk',
	('Monticello', 'NY'): 'Sullivan',
	('Woodward', 'OK'): 'Woodward',
	('Stigler', 'OK'): 'Haskell',
	('Upper Darby', 'PA'): 'Delaware',
	('West Chester', 'PA'): 'Chester',
	('Doylestown', 'PA'): 'Bucks',
	('York', 'PA'): 'York',
	('Beaver Falls', 'PA'): 'Beaver',
	('Pierre', 'SD'): 'Hughe',
    ('Crossville', 'TN'): 'Cumberland',
	('Leesburg,', 'VA'): 'Loudoun',
	('Woodbridge', 'VA'): 'Prince William',
	('Montpelier', 'VT'): 'Washington',
	('Bridgeport', 'WV'): 'Harrison',
}

In [233]:
def city_to_county(city, state):
    print('\t(\'' + city + '\', \'' + state + '\'): \'\',')
    if (city, state) in cache:
        return cache[(city, state)]
    
    if ((city, state) in exceptions):
        return exceptions[(city, state)]
    
    cty = [c for c in gc.search_cities(city, case_sensitive=False) if c['admin1code'] == state][0]
    coords = cty["latitude"], cty["longitude"]
    result = gl.reverse(coords).address.split(", ")[-4]
    cache[(city, state)] = result
    return result

def isState(state):
    return str(state).title() in state_codes

def decountify(s):
    if (s == "Carson City"):
        return
        
    return " ".join([i for i in s.split() if i.lower() not in ["county", "parish", "municipality", "borough", "town", "city"]])

In [11]:
grants_data = "datasets/2007-2022-PIT-Counts-by-CoC.xlsx"
contact_data = "datasets/Grantee_Contacts_02102023_221635169.xls"

In [47]:
grants = pd.read_excel(grants_data)
contacts = pd.read_excel(contact_data, engine='xlrd')

In [84]:
grants

CoC Number  \
0                                               AK-500   
1                                               AK-501   
2                                               AL-500   
3                                               AL-501   
4                                               AL-502   
5                                               AL-503   
6                                               AL-504   
7                                               AL-505   
8                                               AL-506   
9                                               AL-507   
10                                              AR-500   
11                                              AR-501   
12                                              AR-503   
13                                              AR-505   
14                                              AR-508   
15                                              AZ-500   
16                                              AZ-501   
17                                              AZ-502   
18                                              CA-500   
19                                              CA-501   
20                                              CA-502   
21                                              CA-503   
22                                              CA-504   
23                                              CA-505   
24                                              CA-506   
25                                              CA-507   
26                                              CA-508   
27                                              CA-509   
28                                              CA-510   
29                                              CA-511   
30                                              CA-512   
31                                              CA-513   
32                                              CA-514   
33                                              CA-515   
34                                              CA-516   
35                                              CA-517   
36                                              CA-518   
37                                              CA-519   
38                                              CA-520   
39                                              CA-521   
40                                              CA-522   
41                                              CA-523   
42                                              CA-524   
43                                              CA-525   
44                                              CA-526   
45                                              CA-527   
46                                              CA-529   
47                                              CA-530   
48                                              CA-531   
49                                              CA-600   
50                                              CA-601   
51                                              CA-602   
52                                              CA-603   
53                                              CA-604   
54                                              CA-606   
55                                              CA-607   
56                                              CA-608   
57                                              CA-609   
58                                              CA-611   
59                                              CA-612   
60                                              CA-613   
61                                              CA-614   
62                                              CO-500   
63                                              CO-503   
64                                              CO-504   
65                                              CO-505   
66                                              CT-503   
67                                              CT-505   
68                                        

In [48]:
contacts.columns = contact.iloc[2]
contacts = contacts.drop([0,1,2])

In [109]:
contacts

2    State                                           Org Name  \
3       AK                             AK-500 - Anchorage CoC   
4       AK                             AK-500 - Anchorage CoC   
5       AK                             AK-500 - Anchorage CoC   
6       AK               AK-501 - Alaska Balance of State CoC   
7       AK               AK-501 - Alaska Balance of State CoC   
8       AK               AK-501 - Alaska Balance of State CoC   
9       AK               AK-501 - Alaska Balance of State CoC   
10      AK                                             Alaska   
11      AK                                             Alaska   
12      AK                                             Alaska   
13      AK                                             Alaska   
14      AK                                             Alaska   
15      AK                 Alaska Housing Finance Corporation   
16      AK                                      Anchorage, AK   
17      AK                                      Anchorage, AK   
18      AK                                      Anchorage, AK   
19      AL                                       AIDS Alabama   
20      AL                                       AIDS Alabama   
21      AL  AL-500 - Birmingham/Jefferson, Saint Clair, Sh...   
22      AL  AL-500 - Birmingham/Jefferson, Saint Clair, Sh...   
23      AL  AL-500 - Birmingham/Jefferson, Saint Clair, Sh...   
24      AL  AL-501 - Mobile City and County/Baldwin County...   
25      AL  AL-501 - Mobile City and County/Baldwin County...   
26      AL  AL-501 - Mobile City and County/Baldwin County...   
27      AL            AL-502 - Florence/Northwest Alabama CoC   
28      AL            AL-502 - Florence/Northwest Alabama CoC   
29      AL            AL-502 - Florence/Northwest Alabama CoC   
30      AL              AL-503 - Huntsville/North Alabama CoC   
31      AL              AL-503 - Huntsville/North Alabama CoC   
32      AL              AL-503 - Huntsville/North Alabama CoC   
33      AL            AL-504 - Montgomery City and County CoC   
34      AL            AL-504 - Montgomery City and County CoC   
35      AL            AL-504 - Montgomery City and County CoC   
36      AL            AL-506 - Tuscaloosa City and County CoC   
37      AL            AL-506 - Tuscaloosa City and County CoC   
38      AL            AL-506 - Tuscaloosa City and County CoC   
39      AL              AL-507 - Alabama Balance of State CoC   
40      AL              AL-507 - Alabama Balance of State CoC   
41      AL              AL-507 - Alabama Balance of State CoC   
42      AL                                            Alabama   
43      AL                                            Alabama   
44      AL                                            Alabama   
45      AL                                            Alabama   
46      AL                                            Alabama   
47      AL                                            Alabama   
48      AL                                       Anniston, AL   
49      AL                                       Anniston, AL   
50      AL                                         Auburn, AL   
51      AL                                         Auburn, AL   
52      AL                                       Bessemer, AL   
53      AL                                     Birmingham, AL   
54      AL                                     Birmingham, AL   
55      AL                                     Birmingham, AL   
56      AL                                     Birmingham, AL   
57      AL                                     Birmingham, AL   
58      AL                                        Decatur, AL   
59      AL                                         Dothan, AL   
60      AL                                       Florence, AL   
61      AL                                        Gadsden, AL   
62      AL                                        Gadsden, AL   
63      AL         Homeless Care Co

In [335]:
contacts_1 = contacts[['Org Name', 'State', 'POC City', 'POC State']]
contacts_1 = contacts_1[contacts_1['State'] == contacts_1['POC State']]
contacts_1 = contacts_1[['Org Name', 'State', 'POC City', 'POC State']]
contacts_1 = contacts_1.rename(columns={'Org Name': 'name', 'State': 'state', 'POC City': 'city'})
contacts_1 = contacts_1[contacts_1['name'].apply(lambda x: len(x.split(' - ')) > 1 and len(x.split(' - ')[0]) == 6)] 
contacts_1['name'] = contacts_1['name'].apply(lambda x: x.split(' - ')[0])
contacts_1 = contacts_1[contacts_1['state'].apply(lambda x: x in states_list)]
contacts_1 = contacts_1.drop_duplicates().dropna()

In [336]:
contacts_1

2       name state              city POC State
3     AK-500    AK         Anchorage        AK
6     AK-501    AK         Anchorage        AK
7     AK-501    AK            Juneau        AK
21    AL-500    AL        Birmingham        AL
24    AL-501    AL            Mobile        AL
27    AL-502    AL          Florence        AL
30    AL-503    AL        Huntsville        AL
33    AL-504    AL        Montgomery        AL
36    AL-506    AL        Tuscaloosa        AL
39    AL-507    AL        Montgomery        AL
90    AR-500    AR       Little Rock        AR
94    AR-501    AR      Fayetteville        AR
95    AR-501    AR       Little Rock        AR
96    AR-503    AR       Hot Springs        AR
98    AR-503    AR       Little Rock        AR
99    AR-504    AR        Batesville        AR
102   AR-505    AR        Pine Bluff        AR
104   AR-505    AR       Little Rock        AR
105   AR-509    AR       Hot Springs        AR
106   AR-509    AR       Little Rock        AR
155   AZ-500    AZ           Phoenix        AZ
158   AZ-501    AZ            Tucson        AZ
161   AZ-502    AZ           Phoenix        AZ
163   AZ-502    AZ             Tempe        AZ
243   CA-500    CA          San Jose        CA
246   CA-501    CA     San Francisco        CA
249   CA-502    CA           Hayward        CA
252   CA-503    CA        Sacramento        CA
255   CA-504    CA        Santa Rosa        CA
259   CA-505    CA           Concord        CA
263   CA-506    CA           Seaside        CA
266   CA-507    CA        San Rafael        CA
269   CA-508    CA        Santa Cruz        CA
272   CA-509    CA             Ukiah        CA
277   CA-510    CA           Modesto        CA
278   CA-511    CA          Stockton        CA
281   CA-512    CA           Belmont        CA
284   CA-513    CA           Visalia        CA
286   CA-513    CA           Hanford        CA
287   CA-514    CA            Fresno        CA
290   CA-515    CA            Auburn        CA
293   CA-516    CA           Redding        CA
296   CA-517    CA              Napa        CA
299   CA-518    CA       Suisun City        CA
302   CA-519    CA          Oroville        CA
305   CA-520    CA            Merced        CA
308   CA-521    CA          Woodland        CA
311   CA-522    CA            Eureka        CA
314   CA-523    CA           Willows        CA
317   CA-524    CA         Yuba City        CA
320   CA-525    CA       Placerville        CA
323   CA-526    CA           Jackson        CA
326   CA-527    CA         Red Bluff        CA
329   CA-529    CA           Lucerne        CA
332   CA-530    CA            Bishop        CA
335   CA-531    CA            Auburn        CA
338   CA-600    CA       Los Angeles        CA
341   CA-601    CA         San Diego        CA
344   CA-602    CA         Santa Ana        CA
347   CA-603    CA     Santa Barbara        CA
350   CA-604    CA       Bakersfield        CA
353   CA-606    CA        Long Beach        CA
356   CA-607    CA          Pasadena        CA
359   CA-608    CA         Riverside        CA
362   CA-609    CA    San Bernardino        CA
365   CA-611    CA           Ventura        CA
368   CA-612    CA          Glendale        CA
371   CA-613    CA         El Centro        CA
374   CA-614    CA   San Luis Obispo        CA
805   CO-500    CO            Denver        CO
808   CO-503    CO            Denver        CO
811   CO-504    CO  Colorado Springs        CO
867   CT-503    CT        Bridgeport        CT
870   CT-505    CT          Hartford        CT
907   DC-500    DC        Washington        DC
921   DE-500    DE        Wilmington        DE
987   FL-500    FL          Sarasota        FL
990   FL-501    FL             Tampa        FL
994   FL-502    FL    St. Petersburg        FL
997   FL-503    FL          Lakeland        FL
1000  FL-504    FL     Daytona Beach        FL
1003  FL-505    FL   Ft Walton Beach        FL
1006  FL-506    FL       Tallahassee        FL
1009  FL-507    FL           Orlando        FL
1012 

In [261]:
gc.search_cities("Florence", case_sensitive=False)

[{'geonameid': 3176959,
  'name': 'Florence',
  'latitude': 43.77925,
  'longitude': 11.24626,
  'countrycode': 'IT',
  'population': 349296,
  'timezone': 'Europe/Rome',
  'admin1code': '16',
  'alternatenames': ['FLR',
   'Fflorens',
   'Firenca',
   'Firence',
   'Firense',
   'Firenz',
   'Firenze',
   'Firenzi',
   'Flarehncyja',
   'Florans',
   'Floransa',
   'Florenc',
   'Florenca',
   'Florence',
   'Florenceje',
   'Florenci',
   'Florencia',
   'Florencie',
   'Florencij',
   'Florencija',
   'Florencja',
   'Florenco',
   'Florencėjė',
   'Florens',
   'Florensa',
   'Florensiya',
   'Florensya',
   'Florenta',
   'Florentia',
   'Florentzia',
   'Florenz',
   'Florença',
   'Florența',
   'Florâns',
   'Florència',
   'Floréncia',
   'Florénsa',
   'Flórans',
   'Flórens',
   'Lungsod ng Florencia',
   'Sciorenza',
   'fei leng cui',
   'firentsue',
   'florensa',
   'flwrans',
   'flwrns',
   'flwrnsa',
   'flxrens',
   'fu luo lun sa',
   'peullolenseu',
   'phlorens',


In [339]:
contacts_2 = contacts_1
contacts_2['county'] = contacts_2.apply(lambda x: city_to_county(x.city, x.state), axis=1)

	('Anchorage', 'AK'): '',
	('Anchorage', 'AK'): '',
	('Juneau', 'AK'): '',
	('Birmingham', 'AL'): '',
	('Mobile', 'AL'): '',
	('Florence', 'AL'): '',
	('Huntsville', 'AL'): '',
	('Montgomery', 'AL'): '',
	('Tuscaloosa', 'AL'): '',
	('Montgomery', 'AL'): '',
	('Little Rock', 'AR'): '',
	('Fayetteville', 'AR'): '',
	('Little Rock', 'AR'): '',
	('Hot Springs', 'AR'): '',
	('Little Rock', 'AR'): '',
	('Batesville', 'AR'): '',
	('Pine Bluff', 'AR'): '',
	('Little Rock', 'AR'): '',
	('Hot Springs', 'AR'): '',
	('Little Rock', 'AR'): '',
	('Phoenix', 'AZ'): '',
	('Tucson', 'AZ'): '',
	('Phoenix', 'AZ'): '',
	('Tempe', 'AZ'): '',
	('San Jose', 'CA'): '',
	('San Francisco', 'CA'): '',
	('Hayward', 'CA'): '',
	('Sacramento', 'CA'): '',
	('Santa Rosa', 'CA'): '',
	('Concord', 'CA'): '',
	('Seaside', 'CA'): '',
	('San Rafael', 'CA'): '',
	('Santa Cruz', 'CA'): '',
	('Ukiah', 'CA'): '',
	('Modesto', 'CA'): '',
	('Stockton', 'CA'): '',
	('Belmont', 'CA'): '',
	('Visalia', 'CA'): '',
	('Hanford', 'CA

	('Cheyenne', 'WY'): '',


In [340]:
contacts_2

2       name state              city POC State                      county
3     AK-500    AK         Anchorage        AK                   Anchorage
6     AK-501    AK         Anchorage        AK                   Anchorage
7     AK-501    AK            Juneau        AK                      Juneau
21    AL-500    AL        Birmingham        AL            Jefferson County
24    AL-501    AL            Mobile        AL               Mobile County
27    AL-502    AL          Florence        AL                  Lauderdale
30    AL-503    AL        Huntsville        AL              Madison County
33    AL-504    AL        Montgomery        AL           Montgomery County
36    AL-506    AL        Tuscaloosa        AL           Tuscaloosa County
39    AL-507    AL        Montgomery        AL           Montgomery County
90    AR-500    AR       Little Rock        AR              Pulaski County
94    AR-501    AR      Fayetteville        AR           Washington County
95    AR-501    AR       Little Rock        AR              Pulaski County
96    AR-503    AR       Hot Springs        AR              Garland County
98    AR-503    AR       Little Rock        AR              Pulaski County
99    AR-504    AR        Batesville        AR                Independence
102   AR-505    AR        Pine Bluff        AR            Jefferson County
104   AR-505    AR       Little Rock        AR              Pulaski County
105   AR-509    AR       Hot Springs        AR              Garland County
106   AR-509    AR       Little Rock        AR              Pulaski County
155   AZ-500    AZ           Phoenix        AZ             Maricopa County
158   AZ-501    AZ            Tucson        AZ                 Pima County
161   AZ-502    AZ           Phoenix        AZ             Maricopa County
163   AZ-502    AZ             Tempe        AZ             Maricopa County
243   CA-500    CA          San Jose        CA          Santa Clara County
246   CA-501    CA     San Francisco        CA    CAL Fire Northern Region
249   CA-502    CA           Hayward        CA              Alameda County
252   CA-503    CA        Sacramento        CA    CAL Fire Northern Region
255   CA-504    CA        Santa Rosa        CA               Sonoma County
259   CA-505    CA           Concord        CA    CAL Fire Northern Region
263   CA-506    CA           Seaside        CA             Monterey County
266   CA-507    CA        San Rafael        CA    CAL Fire Northern Region
269   CA-508    CA        Santa Cruz        CA    CAL Fire Northern Region
272   CA-509    CA             Ukiah        CA    CAL Fire Northern Region
277   CA-510    CA           Modesto        CA    CAL Fire Southern Region
278   CA-511    CA          Stockton        CA          San Joaquin County
281   CA-512    CA           Belmont        CA    CAL Fire Northern Region
284   CA-513    CA           Visalia        CA               Tulare County
286   CA-513    CA           Hanford        CA                Kings County
287   CA-514    CA            Fresno        CA    CAL Fire Southern Region
290   CA-515    CA            Auburn        CA                      Placer
293   CA-516    CA           Redding        CA    CAL Fire Northern Region
296   CA-517    CA              Napa        CA                 Napa County
299   CA-518    CA       Suisun City        CA               Solano County
302   CA-519    CA          Oroville        CA    CAL Fire Northern Region
305   CA-520    CA            Merced        CA               Merced County
308   CA-521    CA          Woodland        CA                 Yolo County
311   CA-522    CA            Eureka        CA             Humboldt County
314   CA-523    CA           Willows        CA                       Glenn
317   CA-524    CA         Yuba City        CA                      Sutter
320   CA-525    CA       Placerville        CA                   El Dorado
323   CA-526    CA           Jackson        CA                      Amador
326   CA-527    CA       

In [344]:
grants

CoC Number  \
0                                               AK-500   
1                                               AK-501   
2                                               AL-500   
3                                               AL-501   
4                                               AL-502   
5                                               AL-503   
6                                               AL-504   
7                                               AL-505   
8                                               AL-506   
9                                               AL-507   
10                                              AR-500   
11                                              AR-501   
12                                              AR-503   
13                                              AR-505   
14                                              AR-508   
15                                              AZ-500   
16                                              AZ-501   
17                                              AZ-502   
18                                              CA-500   
19                                              CA-501   
20                                              CA-502   
21                                              CA-503   
22                                              CA-504   
23                                              CA-505   
24                                              CA-506   
25                                              CA-507   
26                                              CA-508   
27                                              CA-509   
28                                              CA-510   
29                                              CA-511   
30                                              CA-512   
31                                              CA-513   
32                                              CA-514   
33                                              CA-515   
34                                              CA-516   
35                                              CA-517   
36                                              CA-518   
37                                              CA-519   
38                                              CA-520   
39                                              CA-521   
40                                              CA-522   
41                                              CA-523   
42                                              CA-524   
43                                              CA-525   
44                                              CA-526   
45                                              CA-527   
46                                              CA-529   
47                                              CA-530   
48                                              CA-531   
49                                              CA-600   
50                                              CA-601   
51                                              CA-602   
52                                              CA-603   
53                                              CA-604   
54                                              CA-606   
55                                              CA-607   
56                                              CA-608   
57                                              CA-609   
58                                              CA-611   
59                                              CA-612   
60                                              CA-613   
61                                              CA-614   
62                                              CO-500   
63                                              CO-503   
64                                              CO-504   
65                                              CO-505   
66                                              CT-503   
67                                              CT-505   
68                                        

In [366]:
grants_1 = grants[["CoC Number", 
                   "Overall Homeless, 2022", 
                   "Overall Homeless - Under 18, 2022", 
                   "Overall Homeless - Age 18 to 24, 2022",
                   "Overall Homeless - Male, 2022",
                   "Overall Homeless - Female, 2022"]]
grants_1 = grants_1.rename(columns={"CoC Number": "name", 
                            "Overall Homeless, 2022": "overall pop",
                            "Overall Homeless - Under 18, 2022": "u18 pop",
                            "Overall Homeless - Age 18 to 24, 2022": "18-24 pop",
                            "Overall Homeless - Male, 2022": "male pop",
                            "Overall Homeless - Female, 2022": "female pop"})
grants_2 = pd.merge(grants_1, contacts_2).drop(columns=["POC State"])
grants_2 = grants_2[["state", "county", "overall pop", "u18 pop", "18-24 pop", "male pop", "female pop"]]
grants_2


state                      county  overall pop  u18 pop  18-24 pop  \
0      AK                   Anchorage       1494.0    182.0      145.0   
1      AK                   Anchorage        826.0    146.0       58.0   
2      AK                      Juneau        826.0    146.0       58.0   
3      AL            Jefferson County        943.0     82.0       43.0   
4      AL               Mobile County        585.0    148.0       30.0   
5      AL                  Lauderdale        232.0     56.0       18.0   
6      AL              Madison County        549.0    106.0       38.0   
7      AL           Montgomery County        278.0     28.0       13.0   
8      AL           Tuscaloosa County         40.0      4.0        0.0   
9      AL           Montgomery County        935.0    364.0       64.0   
10     AR              Pulaski County        859.0    103.0      133.0   
11     AR           Washington County        343.0     80.0       16.0   
12     AR              Pulaski County        343.0     80.0       16.0   
13     AR              Garland County        814.0     50.0       87.0   
14     AR              Pulaski County        814.0     50.0       87.0   
15     AR            Jefferson County         69.0     10.0        7.0   
16     AR              Pulaski County         69.0     10.0        7.0   
17     AZ             Maricopa County       2300.0    251.0      110.0   
18     AZ                 Pima County       2227.0    232.0      225.0   
19     AZ             Maricopa County       9026.0   1240.0      749.0   
20     AZ             Maricopa County       9026.0   1240.0      749.0   
21     CA          Santa Clara County      10028.0    539.0     1190.0   
22     CA    CAL Fire Northern Region       7754.0    423.0     1029.0   
23     CA              Alameda County       9747.0    583.0      804.0   
24     CA    CAL Fire Northern Region       9278.0    778.0      636.0   
25     CA               Sonoma County       2893.0    106.0      507.0   
26     CA    CAL Fire Northern Region       3093.0    106.0      228.0   
27     CA             Monterey County       2404.0    241.0      226.0   
28     CA    CAL Fire Northern Region       1121.0    139.0      140.0   
29     CA    CAL Fire Northern Region       2299.0     92.0      237.0   
30     CA    CAL Fire Northern Region        830.0     71.0       43.0   
31     CA    CAL Fire Southern Region       1857.0    183.0       92.0   
32     CA          San Joaquin County       2319.0    329.0       96.0   
33     CA    CAL Fire Northern Region       1808.0    216.0       72.0   
34     CA               Tulare County       1235.0     87.0       70.0   
35     CA                Kings County       1235.0     87.0       70.0   
36     CA    CAL Fire Southern Region       4216.0    464.0      129.0   
37     CA                      Placer        750.0     59.0       43.0   
38     CA    CAL Fire Northern Region       1837.0    218.0       97.0   
39     CA                 Napa County        495.0     17.0       29.0   
40     CA               Solano County       1179.0     65.0       67.0   
41     CA    CAL Fire Northern Region       1006.0     95.0       44.0   
42     CA               Merced County        855.0    152.0       63.0   
43     CA                 Yolo County        746.0     91.0       47.0   
44     CA             Humboldt County       1648.0     47.0       61.0   
45     CA                       Glenn        340.0    107.0       16.0   
46     CA                      Sutter       1094.0    276.0       64.0   
47     CA                   El Dorado        511.0     14.0       84.0   
48     CA                      Amador        625.0     49.0       28.0   
49     CA                      Tehama        291.0     40.0       14.0   
50     CA                        Lake        339.0     27.0       25.0   
51     CA                        Inyo        140.0     31.0        7.0   
52     CA                      Placer        527.0     60.0       25.0   
53     C

In [367]:
grants = grants_2

In [368]:
grants.to_csv("./dataframes/pit.csv")